In [1]:
import os, re, sys, pandas as pd
TXT_DIR = '/Users/heejinohn/trantxt/txt'
csv = 'master_csv.csv'

In [9]:
with open(r'/Users/heejinohn/trantxt/master_csv.csv', 'r') as csvfile:
    for linenum, line in enumerate(csvfile):
        splitted_line = line.split(",")
        filename = splitted_line[1].rstrip()
        cusip = splitted_line[0].rstrip()
        print(linenum, filename, " started.")
#####################################################################################
# read in file
#####################################################################################
        file = open(os.path.join(TXT_DIR, filename),'r')
        text = file.read()
        file.close()
#####################################################################################
# split lines 
#####################################################################################
        lines = [line.strip() for line in text.split('\n')]
        lines = [' '.join(x.split()) for x in lines if x=='' or len(x) >= 3]
        if next(s for s in lines if s) == 'Corrected Transcript':
            doc_error = 0
            doc = next((x for x in lines if x.endswith('Transcript')), None)
            pat1 = re.compile(r"^(([0-9])|([0-2][0-9])|([3][0-1]))[- /.](Jan|Feb|Mar|Apr|May|Jun|Jul|Aug|Sep|Oct|Nov|Dec)[- /.](19|20)\d\d$")
            date = next((x for x in lines if pat1.match(x)), None)
            pat2 = re.compile(r"^(?:.*)\s\((?:[A-Z]+(?:\.XX(?:[0-9]|1[0-9])|\.[A-Z]+(?:\.[A-Z]+)?|\s?Q[0-5])?|[0-9A-Z]+\-[A-Z])\)$")
            comp = next((x for x in lines if pat2.match(x)), None)
            pat4 = re.compile(r"^((March|September|December|FY|Q[1-5])\s+\d{4}\s+|Business Update)")
            evnt = next((x for x in lines if pat4.match(x)), None)
            if comp is not None:
                tic = comp[comp.find("(")+1:comp.find(")")]
            else:
                tic = ""
#####################################################################################
# write doc file for documents other than corrected transcripts
#####################################################################################
        else:
            doc_error = 1
            doc = pd.DataFrame(data = [(cusip, 1, "", "")],index=[filename])
            doc.to_csv(r'/Users/heejinohn/trantxt/doc.csv', mode='a', header=False, sep='|')
            print('\t', linenum, filename, ' completed.')
# All subsequent codes apply only to documents identified as corrected transcripts.


        if doc_error == 0:
#####################################################################################
# remove clutters
#####################################################################################
            lines = [line for line in lines if line[:5]!="1-877" \
                     and line.split(' ', 1)[0]!='Copyright' \
                     and line.split(':', 1)[0]!='Total Pages' \
                     and line != date \
                     and "".join(line.split()) != "".join(comp.split()) \
                     and line != evnt \
                     and line != doc \
                     and line != "("+tic+")"
                    ]
            discl = len(lines) - 1 - lines[::-1].index('Disclaimer')
            lines = lines[:discl]
            from itertools import groupby
            lines = [x[0] for x in groupby(lines)]
            clean_txt = lines.copy()
#####################################################################################
# identify management:position
#####################################################################################
            # def chunks(l, n):
            #     chunk=[]
            #     """Yield successive n-sized chunks from l."""
            #     for i in range(0, len(l), n):
            #         chunk.append(l[i:i + n])
            #     return chunk

            if "CORPORATE PARTICIPANTS" in clean_txt:
                start = len(clean_txt) - 1 - clean_txt[::-1].index('CORPORATE PARTICIPANTS')
                end = next(i for i, x in enumerate(clean_txt) if x.startswith('......') or x == 'OTHER PARTICIPANTS')
                blanks = [i for i, x in enumerate(clean_txt[start:end]) if x=='']
                mgmt_names =[clean_txt[start:end][blanks[i]+1] for i in range(len(blanks)-1)]
                mgmt_pos = []
                for i in range(len(blanks)-1):
                    if blanks[i+1] - blanks[i]==3:
                        mgmt_pos.append(clean_txt[start:end][blanks[i]+2])
                    else:
                        pos = " ".join(clean_txt[start:end][blanks[i]+2:blanks[i+1]])
                        mgmt_pos.append(pos)
                mgmt_error = 0
                del clean_txt[:end + 1]
                mgmt = pd.DataFrame(data = list(zip(mgmt_names,mgmt_pos)), index = [[filename] * len(mgmt_names), list(range(len(mgmt_names)))])
                mgmt.to_csv(r'/Users/heejinohn/trantxt/mgmt.csv', mode='a', header=False, sep='|')
            else:
                mgmt_error = 1
                mgmt = pd.DataFrame(data = [("", 1, "", "")],index=[filename])
                mgmt.to_csv(r'/Users/heejinohn/trantxt/mgmt.csv', mode='a', header=False, sep='|')


#####################################################################################
# identify analyst:firm
#####################################################################################
            if "OTHER PARTICIPANTS" in clean_txt:
                start = len(clean_txt) - 1 - clean_txt[::-1].index('OTHER PARTICIPANTS')
                end = next(i for i, x in enumerate(clean_txt) if x.startswith('......') or x == 'MANAGEMENT DISCUSSION SECTION')
                blanks = [i for i, x in enumerate(clean_txt[start:end]) if x=='']
                analyst_names =[clean_txt[start:end][blanks[i]+1] for i in range(len(blanks)-1)]
                analyst_emps = []
                for i in range(len(blanks)-1):
                    if blanks[i+1] - blanks[i]==3:
                        analyst_emps.append(clean_txt[start:end][blanks[i]+2])
                    else:
                        pos = " ".join(clean_txt[start:end][blanks[i]+2:blanks[i+1]])
                        analyst_emps.append(pos)
                analyst_error = 0
                del clean_txt[:end + 1]
                analyst = pd.DataFrame(data = list(zip(analyst_names,analyst_emps)), index = [[filename] * len(analyst_names), list(range(len(analyst_names)))])
                analyst.to_csv(r'/Users/heejinohn/trantxt/analysts.csv', mode='a', header=False, sep='|')
            else:
                analyst_error = 1
                analyst = pd.DataFrame(data = [("", 1, "", "")],index=[filename])
                analyst.to_csv(r'/Users/heejinohn/trantxt/analysts.csv', mode='a', header=False, sep='|')

#####################################################################################
# remove operator dialogues
#####################################################################################
            clean_txt = [i for i in clean_txt if i != ""]
            operators = [i for i, x in enumerate(clean_txt) if x[:9] == "Operator:"]
            splits = [i for i, x in enumerate(clean_txt) if x.startswith('......') or x in analyst_names + mgmt_names]
            drops = [[x,next((i for i in splits if i > x), None)] for x in operators]
            for x in drops[::-1]:
                if x[1] == None:
                    del clean_txt[x[0]:]
                else:
                    if x[1]-x[0]==1:
                        del clean_txt[x[0]]
                    else:
                        del clean_txt[x[0]:x[1]]
#####################################################################################
# divide management discussion and question and answer sections
#####################################################################################
            if 'QUESTION AND ANSWER SECTION' in clean_txt:
                sec = clean_txt.index('QUESTION AND ANSWER SECTION')
                mds = clean_txt[:sec]
                qnas = clean_txt[sec + 1:]
                qnas_error = 0
            else:
                mds = clean_txt
                qna_clean_txt = ""
                qnas_error = 1
#####################################################################################
# clean management discussion section
#####################################################################################
            mds_clean = [x for x in mds if x not in mgmt_names \
                        and x not in mgmt_pos \
                        and not x.startswith('......') \
                        and (x != x.upper() or not re.search('[a-zA-Z]', x))]
            mds_clean_txt = " ".join(mds_clean)
#####################################################################################
# write doc file for corrected transcripts
#####################################################################################
            doc = pd.DataFrame(data = [(cusip, doc_error, qnas_error, mds_clean_txt)],index=[filename])
            doc.to_csv(r'/Users/heejinohn/trantxt/doc.csv', mode='a', header=False, sep='|')
#####################################################################################
# clean question and answer section
#####################################################################################
            if mgmt_error == 0 and analyst_error == 0 and qnas_error == 0:
                qnas_clean = [x for x in qnas if x.startswith('.......') \
                              or x.upper() != x or not re.search('[a-zA-Z]', x)]
                qnas_clean = [x for x in qnas_clean if x not in mgmt_pos and x not in analyst_emps]
                for n, i in enumerate(qnas_clean):
                    if i.startswith('<'):
                        if ':' in i:
                            qnas_clean.insert(n+1, i.split(':',1)[1])
                            split_i = i.split(':',1)[0]
                        elif ']' in i:
                            qnas_clean.insert(n+1, i.split(']',1)[1])
                            split_i = i.split(']',1)[0]
                        else:
                            split_i = i
                        capped = set(re.findall(r'(\b[A-Z][a-zA-Z\'\-]+\b)', split_i))
                        if not capped:
                            capped = set(re.findall(r'(\b[A-Z][a-zA-Z\'\-]+\b)', i))
                        a_last = [i[-1] for i in [i.split() for i in analyst_names]]
                        a_first = [j for fullname in analyst_names for j in fullname.split()[:-1]]
                        m_last = [i[-1] for i in [i.split() for i in mgmt_names]]
                        m_first = [j for fullname in mgmt_names for j in fullname.split()[:-1]]
                        if capped&set(a_last) and not capped&set(m_last):
                            if len(capped&set(a_last)) == 1:
                                qnas_clean[n] = analyst_names[a_last.index(next(iter(capped&set(a_last))))]
                            else:
                                qnas_clean[n] = analyst_names[a_first.index(next(iter(capped&set(a_first))))]
                        elif capped&set(m_last) and not capped&set(a_last):
                            if len(capped&set(m_last)) == 1:
                                qnas_clean[n] = mgmt_names[m_last.index(next(iter(capped&set(m_last))))]
                            else:
                                qnas_clean[n] = mgmt_names[m_first.index(next(iter(capped&set(m_first))))]
                        else:
                            if capped&set(a_first):
                                qnas_clean[n] = analyst_names[a_last.index(next(iter(capped&set(a_last))))]
                            elif capped&set(m_first):
                                qnas_clean[n] = mgmt_names[m_last.index(next(iter(capped&set(m_last))))]
                
                splits = [i for i, x in enumerate(qnas_clean) if x.startswith('......')]
                mgmt_locs = [i for i, x in enumerate(qnas_clean) if x in mgmt_names]
                analyst_locs = [i for i, x in enumerate(qnas_clean) if x in analyst_names]
                sides = []
                for split in splits:
                    if split == 0:
                        sides.append(split + 1)
                    else:
                        sides.extend([split - 1, split + 1])
                add_splits = [x for x in list(set(mgmt_locs)-set(sides))+list(set(analyst_locs)-set(sides))]
                combines = sorted(splits + add_splits)
                qna_clean_txt = []
                for i in range(len(combines)-1):
                    if combines[i] in splits and combines[i+1]-combines[i] > 1:
                        qna_clean_txt.append(qnas_clean[combines[i]+1])
                        qna_clean_txt.append(" ".join(qnas_clean[combines[i]+2:combines[i+1]]))
                    elif combines[i] in add_splits and combines[i+1]-combines[i] > 1:
                        qna_clean_txt.append(qnas_clean[combines[i]])
                        qna_clean_txt.append(" ".join(qnas_clean[combines[i]+1:combines[i+1]]))
                if combines[-1] != len(qnas_clean):
                    if combines[-1] in splits and len(qnas_clean)-combines[-1] > 1:
                        qna_clean_txt.append(qnas_clean[combines[-1]+1])
                        qna_clean_txt.append(" ".join(qnas_clean[combines[-1]+2:]))
                    elif combines[-1] in add_splits and len(qnas_clean)-combines[-1] > 1:
                        qna_clean_txt.append(qnas_clean[combines[-1]])
                        qna_clean_txt.append(" ".join(qnas_clean[combines[-1]+1:]))
                an_emp = dict(zip(analyst_names, analyst_emps))
                an_loc = {analyst:qna_clean_txt.index(analyst) for analyst in analyst_names if analyst in qna_clean_txt}
                analyst_names = sorted(analyst_names, key = lambda x: (x not in an_loc, an_loc.get(x, None)))
                analyst_emp = [an_emp[name] for name in analyst_names]
                q = dict()
                l = dict()

                for i, name in enumerate(analyst_names):
                    q[i] = [qna_clean_txt[j+1] for j, line in enumerate(qna_clean_txt) if line == name]
                    l[i] = [j+1 for j, line in enumerate(qna_clean_txt) if line == name]
                a = {k: [] for k in list(l.keys())}
                
                for key in l.keys():
                    if len(l[key]) > 0:
                        others = [name for i, name in enumerate(analyst_names) if i != key]
                        for n, loc in enumerate(l[key][:-1]):
                            end = min(l[key][n+1], next((i for i, line in enumerate(qna_clean_txt) if line in others and i > loc), len(qna_clean_txt)))
                            if any(x in mgmt_names for x in qna_clean_txt[loc:end]):
                                a[key].append(" ".join([qna_clean_txt[loc:end][j+1] for j,line in enumerate(qna_clean_txt[loc:end]) if line in mgmt_names]))
                            else:
                                a[key].append("")
                        if l[key][-1] == max(value for values in l.values() for value in values):
                            if len([x for x in q[key][-1].split(". ") if not re.search(r'[T|t]hanks?(?:\syou)?|appreciate|[O|o]kay|[G|g]ood|[G|g]reat|[Y|y]eah', x)]) < 3:
                                a[key].append("")
                            else:
                                if any(x in mgmt_names for x in qna_clean_txt[l[key][-1]:]):
                                    a[key].append(" ".join([qna_clean_txt[l[key][-1]:][j+1] for j,line in enumerate(qna_clean_txt[l[key][-1]:]) if line in mgmt_names]))
                                else:
                                    a[key].append("")
                        else:
                            end = next(i for i, line in enumerate(qna_clean_txt) if line in others and i > l[key][-1])
                            if any(x in mgmt_names for x in qna_clean_txt[l[key][-1]:end]):
                                a[key].append(" ".join([qna_clean_txt[l[key][-1]:end][j+1] for j,line in enumerate(qna_clean_txt[l[key][-1]:end]) if line in mgmt_names]))
                            else:
                                a[key].append("")
#####################################################################################
# write qna file
#####################################################################################                            
                index = pd.MultiIndex.from_tuples([(filename, key, i) for key in q for i in range(len(q[key]))])
                qa = pd.DataFrame(index = index, columns =['q', 'a'])
                for key in q:
                    if len(q[key]) > 0:
                        for i in range(len(q[key])):
                            qa.at[(filename, key, i), "q"] = q[key][i]
                            qa.at[(filename, key, i), "a"] = a[key][i]
                qa.to_csv(r'/Users/heejinohn/trantxt/qna.csv', mode='a', header=False, sep='|')
#####################################################################################
# clean slate
#####################################################################################                                            
            for name in dir():
                if name in ['doc', 'mgmt', 'analyst', 'qa']:
                    del globals() [name]
            print('\t', linenum, filename, ' completed.')

0 MAC_20040805.pdf.txt  started.
	 0 MAC_20040805.pdf.txt  completed.
1 MAC_20041105.pdf.txt  started.
	 1 MAC_20041105.pdf.txt  completed.
2 MAC_20050210.pdf.txt  started.
	 2 MAC_20050210.pdf.txt  completed.
3 MAC_20050502.pdf.txt  started.
	 3 MAC_20050502.pdf.txt  completed.
4 MAC_20050804.pdf.txt  started.
	 4 MAC_20050804.pdf.txt  completed.
5 MAC_20051108.pdf.txt  started.
	 5 MAC_20051108.pdf.txt  completed.
6 MAC_20060214.pdf.txt  started.
	 6 MAC_20060214.pdf.txt  completed.
7 MAC_20060803.pdf.txt  started.
	 7 MAC_20060803.pdf.txt  completed.
8 MAC_20061103.pdf.txt  started.
	 8 MAC_20061103.pdf.txt  completed.
9 MAC_20070213.pdf.txt  started.
	 9 MAC_20070213.pdf.txt  completed.
10 MAC_20070504.pdf.txt  started.
	 10 MAC_20070504.pdf.txt  completed.
11 MAC_20070802.pdf.txt  started.
	 11 MAC_20070802.pdf.txt  completed.
12 MAC_20071031.pdf.txt  started.
	 12 MAC_20071031.pdf.txt  completed.
13 MAC_20080212.pdf.txt  started.
	 13 MAC_20080212.pdf.txt  completed.
14 MAC_20080

	 112 MAG.XX1_20051101.pdf.txt  completed.
113 MAG.XX1_20060202.pdf.txt  started.
	 113 MAG.XX1_20060202.pdf.txt  completed.
114 MAG.XX1_20060929.pdf.txt  started.
	 114 MAG.XX1_20060929.pdf.txt  completed.
115 MAG.XX1_20061110.pdf.txt  started.
	 115 MAG.XX1_20061110.pdf.txt  completed.
116 MAG.XX1_20070501.pdf.txt  started.
	 116 MAG.XX1_20070501.pdf.txt  completed.
117 MAG.XX1_20070822.pdf.txt  started.
	 117 MAG.XX1_20070822.pdf.txt  completed.
118 MAG.XX1_20071031.pdf.txt  started.
	 118 MAG.XX1_20071031.pdf.txt  completed.
119 MAG.XX1_20080206.pdf.txt  started.
	 119 MAG.XX1_20080206.pdf.txt  completed.
120 MAG.XX1_20080429.pdf.txt  started.
	 120 MAG.XX1_20080429.pdf.txt  completed.
121 MAG.XX1_20080813.pdf.txt  started.
	 121 MAG.XX1_20080813.pdf.txt  completed.
122 MAG.XX1_20081029.pdf.txt  started.
	 122 MAG.XX1_20081029.pdf.txt  completed.
123 MAG.XX1_20090205.pdf.txt  started.
	 123 MAG.XX1_20090205.pdf.txt  completed.
124 MAG.XX1_20090508.pdf.txt  started.
	 124 MAG.XX1_20

	 219 MAM_20051110.pdf.txt  completed.
220 MAN_20030415.pdf.txt  started.
	 220 MAN_20030415.pdf.txt  completed.
221 MAN_20030717.pdf.txt  started.
	 221 MAN_20030717.pdf.txt  completed.
222 MAN_20031016.pdf.txt  started.
	 222 MAN_20031016.pdf.txt  completed.
223 MAN_20040129.pdf.txt  started.
	 223 MAN_20040129.pdf.txt  completed.
224 MAN_20040419.pdf.txt  started.
	 224 MAN_20040419.pdf.txt  completed.
225 MAN_20040720.pdf.txt  started.
	 225 MAN_20040720.pdf.txt  completed.
226 MAN_20041019.pdf.txt  started.
	 226 MAN_20041019.pdf.txt  completed.
227 MAN_20050201.pdf.txt  started.
	 227 MAN_20050201.pdf.txt  completed.
228 MAN_20050419.pdf.txt  started.
	 228 MAN_20050419.pdf.txt  completed.
229 MAN_20050719.pdf.txt  started.
	 229 MAN_20050719.pdf.txt  completed.
230 MAN_20051019.pdf.txt  started.
	 230 MAN_20051019.pdf.txt  completed.
231 MAN_20060127.pdf.txt  started.
	 231 MAN_20060127.pdf.txt  completed.
232 MAN_20060418.pdf.txt  started.
	 232 MAN_20060418.pdf.txt  completed.

	 330 MANH_20150203.pdf.txt  completed.
331 MANH_20150421.pdf.txt  started.
	 331 MANH_20150421.pdf.txt  completed.
332 MANH_20150721.pdf.txt  started.
	 332 MANH_20150721.pdf.txt  completed.
333 MANH_20151020.pdf.txt  started.
	 333 MANH_20151020.pdf.txt  completed.
334 MANH_20160202.pdf.txt  started.
	 334 MANH_20160202.pdf.txt  completed.
335 MANH_20160419.pdf.txt  started.
	 335 MANH_20160419.pdf.txt  completed.
336 MANH_20160719.pdf.txt  started.
	 336 MANH_20160719.pdf.txt  completed.
337 MANH_20161018.pdf.txt  started.
	 337 MANH_20161018.pdf.txt  completed.
338 MANH_20170131.pdf.txt  started.
	 338 MANH_20170131.pdf.txt  completed.
339 MANH_20170420.pdf.txt  started.
	 339 MANH_20170420.pdf.txt  completed.
340 MANH_20170720.pdf.txt  started.
	 340 MANH_20170720.pdf.txt  completed.
341 MANH_20171024.pdf.txt  started.
	 341 MANH_20171024.pdf.txt  completed.
342 MANH_20180206.pdf.txt  started.
	 342 MANH_20180206.pdf.txt  completed.
343 MANT_20030730.pdf.txt  started.
	 343 MANT_2

	 440 MAR_20090423.pdf.txt  completed.
441 MAR_20090716.pdf.txt  started.
	 441 MAR_20090716.pdf.txt  completed.
442 MAR_20091008.pdf.txt  started.
	 442 MAR_20091008.pdf.txt  completed.
443 MAR_20100211.pdf.txt  started.
	 443 MAR_20100211.pdf.txt  completed.
444 MAR_20100422.pdf.txt  started.
	 444 MAR_20100422.pdf.txt  completed.
445 MAR_20100715.pdf.txt  started.
	 445 MAR_20100715.pdf.txt  completed.
446 MAR_20101007.pdf.txt  started.
	 446 MAR_20101007.pdf.txt  completed.
447 MAR_20110215.pdf.txt  started.
	 447 MAR_20110215.pdf.txt  completed.
448 MAR_20110421.pdf.txt  started.
	 448 MAR_20110421.pdf.txt  completed.
449 MAR_20110714.pdf.txt  started.
	 449 MAR_20110714.pdf.txt  completed.
450 MAR_20111006.pdf.txt  started.
	 450 MAR_20111006.pdf.txt  completed.
451 MAR_20120216.pdf.txt  started.
	 451 MAR_20120216.pdf.txt  completed.
452 MAR_20120419.pdf.txt  started.
	 452 MAR_20120419.pdf.txt  completed.
453 MAR_20120712.pdf.txt  started.
	 453 MAR_20120712.pdf.txt  completed.

...

	 71036 ZION_20080717.pdf.txt  completed.
71037 ZION_20081016.pdf.txt  started.
	 71037 ZION_20081016.pdf.txt  completed.
71038 ZION_20090126.pdf.txt  started.
	 71038 ZION_20090126.pdf.txt  completed.
71039 ZION_20090420.pdf.txt  started.
	 71039 ZION_20090420.pdf.txt  completed.
71040 ZION_20090720.pdf.txt  started.
	 71040 ZION_20090720.pdf.txt  completed.
71041 ZION_20091019.pdf.txt  started.
	 71041 ZION_20091019.pdf.txt  completed.
71042 ZION_20100125.pdf.txt  started.
	 71042 ZION_20100125.pdf.txt  completed.
71043 ZION_20100419.pdf.txt  started.
	 71043 ZION_20100419.pdf.txt  completed.
71044 ZION_20100719.pdf.txt  started.
	 71044 ZION_20100719.pdf.txt  completed.
71045 ZION_20101018.pdf.txt  started.
	 71045 ZION_20101018.pdf.txt  completed.
71046 ZION_20110124.pdf.txt  started.
	 71046 ZION_20110124.pdf.txt  completed.
71047 ZION_20110418.pdf.txt  started.
	 71047 ZION_20110418.pdf.txt  completed.
71048 ZION_20110718.pdf.txt  started.
	 71048 ZION_20110718.pdf.txt  completed

	 71139 ZIXI_20121023.pdf.txt  completed.
71140 ZIXI_20130219.pdf.txt  started.
	 71140 ZIXI_20130219.pdf.txt  completed.
71141 ZIXI_20130423.pdf.txt  started.
	 71141 ZIXI_20130423.pdf.txt  completed.
71142 ZIXI_20130723.pdf.txt  started.
	 71142 ZIXI_20130723.pdf.txt  completed.
71143 ZIXI_20131022.pdf.txt  started.
	 71143 ZIXI_20131022.pdf.txt  completed.
71144 ZIXI_20140218.pdf.txt  started.
	 71144 ZIXI_20140218.pdf.txt  completed.
71145 ZIXI_20140422.pdf.txt  started.
	 71145 ZIXI_20140422.pdf.txt  completed.
71146 ZIXI_20140722.pdf.txt  started.
	 71146 ZIXI_20140722.pdf.txt  completed.
71147 ZIXI_20141021.pdf.txt  started.
	 71147 ZIXI_20141021.pdf.txt  completed.
71148 ZIXI_20150217.pdf.txt  started.
	 71148 ZIXI_20150217.pdf.txt  completed.
71149 ZIXI_20150421.pdf.txt  started.
	 71149 ZIXI_20150421.pdf.txt  completed.
71150 ZIXI_20150721.pdf.txt  started.
	 71150 ZIXI_20150721.pdf.txt  completed.
71151 ZIXI_20151020.pdf.txt  started.
	 71151 ZIXI_20151020.pdf.txt  completed

	 71244 ZNGA_20130725.pdf.txt  completed.
71245 ZNGA_20131024.pdf.txt  started.
	 71245 ZNGA_20131024.pdf.txt  completed.
71246 ZNGA_20140130.pdf.txt  started.
	 71246 ZNGA_20140130.pdf.txt  completed.
71247 ZNGA_20140423.pdf.txt  started.
	 71247 ZNGA_20140423.pdf.txt  completed.
71248 ZNGA_20140807.pdf.txt  started.
	 71248 ZNGA_20140807.pdf.txt  completed.
71249 ZNGA_20141106.pdf.txt  started.
	 71249 ZNGA_20141106.pdf.txt  completed.
71250 ZNGA_20150212.pdf.txt  started.
	 71250 ZNGA_20150212.pdf.txt  completed.
71251 ZNGA_20150506.pdf.txt  started.
	 71251 ZNGA_20150506.pdf.txt  completed.
71252 ZNGA_20150806.pdf.txt  started.
	 71252 ZNGA_20150806.pdf.txt  completed.
71253 ZNGA_20151103.pdf.txt  started.
	 71253 ZNGA_20151103.pdf.txt  completed.
71254 ZNGA_20160210.pdf.txt  started.
	 71254 ZNGA_20160210.pdf.txt  completed.
71255 ZNGA_20160504.pdf.txt  started.
	 71255 ZNGA_20160504.pdf.txt  completed.
71256 ZNGA_20160804.pdf.txt  started.
	 71256 ZNGA_20160804.pdf.txt  completed

	 71349 ZQKSQ_20040909.pdf.txt  completed.
71350 ZQKSQ_20041216.pdf.txt  started.
	 71350 ZQKSQ_20041216.pdf.txt  completed.
71351 ZQKSQ_20050310.pdf.txt  started.
	 71351 ZQKSQ_20050310.pdf.txt  completed.
71352 ZQKSQ_20050606.pdf.txt  started.
	 71352 ZQKSQ_20050606.pdf.txt  completed.
71353 ZQKSQ_20050908.pdf.txt  started.
	 71353 ZQKSQ_20050908.pdf.txt  completed.
71354 ZQKSQ_20051216.pdf.txt  started.
	 71354 ZQKSQ_20051216.pdf.txt  completed.
71355 ZQKSQ_20060309.pdf.txt  started.
	 71355 ZQKSQ_20060309.pdf.txt  completed.
71356 ZQKSQ_20060907.pdf.txt  started.
	 71356 ZQKSQ_20060907.pdf.txt  completed.
71357 ZQKSQ_20070308.pdf.txt  started.
	 71357 ZQKSQ_20070308.pdf.txt  completed.
71358 ZQKSQ_20070608.pdf.txt  started.
	 71358 ZQKSQ_20070608.pdf.txt  completed.
71359 ZQKSQ_20070906.pdf.txt  started.
	 71359 ZQKSQ_20070906.pdf.txt  completed.
71360 ZQKSQ_20071213.pdf.txt  started.
	 71360 ZQKSQ_20071213.pdf.txt  completed.
71361 ZQKSQ_20080307.pdf.txt  started.
	 71361 ZQKSQ_20

	 71453 ZUMZ_20080313.pdf.txt  completed.
71454 ZUMZ_20080522.pdf.txt  started.
	 71454 ZUMZ_20080522.pdf.txt  completed.
71455 ZUMZ_20080821.pdf.txt  started.
	 71455 ZUMZ_20080821.pdf.txt  completed.
71456 ZUMZ_20081120.pdf.txt  started.
	 71456 ZUMZ_20081120.pdf.txt  completed.
71457 ZUMZ_20090312.pdf.txt  started.
	 71457 ZUMZ_20090312.pdf.txt  completed.
71458 ZUMZ_20090521.pdf.txt  started.
	 71458 ZUMZ_20090521.pdf.txt  completed.
71459 ZUMZ_20090820.pdf.txt  started.
	 71459 ZUMZ_20090820.pdf.txt  completed.
71460 ZUMZ_20091119.pdf.txt  started.
	 71460 ZUMZ_20091119.pdf.txt  completed.
71461 ZUMZ_20100311.pdf.txt  started.
	 71461 ZUMZ_20100311.pdf.txt  completed.
71462 ZUMZ_20100520.pdf.txt  started.
	 71462 ZUMZ_20100520.pdf.txt  completed.
71463 ZUMZ_20100819.pdf.txt  started.
	 71463 ZUMZ_20100819.pdf.txt  completed.
71464 ZUMZ_20101201.pdf.txt  started.
	 71464 ZUMZ_20101201.pdf.txt  completed.
71465 ZUMZ_20110310.pdf.txt  started.
	 71465 ZUMZ_20110310.pdf.txt  completed